In [1]:
import requests
import re
import time
import pandas as pd

from bs4 import BeautifulSoup
from IPython.core.display import HTML

In [2]:
# Get the Wikipedia page
req = requests.get('https://en.wikipedia.org/wiki/Lists_of_mathematicians')

# get text of page
page = req.text

# convert page into BeautifulSoup object
soup = BeautifulSoup(page, 'html.parser')
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   Lists of mathematicians - Wikipedia
  </title>
  <script>
   document.documentElement.className = document.documentElement.className.replace( /(^|\s)client-nojs(\s|$)/, "$1client-js$2" );
  </script>
  <script>
   (window.RLQ=window.RLQ||[]).push(function(){mw.config.set({"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Lists_of_mathematicians","wgTitle":"Lists of mathematicians","wgCurRevisionId":794820352,"wgRevisionId":794820352,"wgArticleId":80143,"wgIsArticle":true,"wgIsRedirect":false,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Lists of mathematicians","Lists of lists","Lists of people in STEM fields"],"wgBreakFrames":false,"wgPageContentLanguage":"en","wgPageContentModel":"wikitext","wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["

In [3]:
# find table containing a list of a list of mathematicians in alphabetical order
table_html = str(soup.find("table", "vertical-navbox"))
# print(table_html)

# confirm table is correct
HTML(table_html)

In [4]:
# find all relevant links in table (i.e. links to sub-lists)
rows = [row for row in soup.find("table", "vertical-navbox").find_all('a')]
rows = [i for i in rows if '"List of mathematicians ' in str(i)]
rows

[<a href="/wiki/List_of_mathematicians_(A)" title="List of mathematicians (A)">A</a>,
 <a href="/wiki/List_of_mathematicians_(B)" title="List of mathematicians (B)">B</a>,
 <a href="/wiki/List_of_mathematicians_(C)" title="List of mathematicians (C)">C</a>,
 <a href="/wiki/List_of_mathematicians_(D)" title="List of mathematicians (D)">D</a>,
 <a href="/wiki/List_of_mathematicians_(E)" title="List of mathematicians (E)">E</a>,
 <a href="/wiki/List_of_mathematicians_(F)" title="List of mathematicians (F)">F</a>,
 <a href="/wiki/List_of_mathematicians_(G)" title="List of mathematicians (G)">G</a>,
 <a href="/wiki/List_of_mathematicians_(H)" title="List of mathematicians (H)">H</a>,
 <a href="/wiki/List_of_mathematicians_(I)" title="List of mathematicians (I)">I</a>,
 <a href="/wiki/List_of_mathematicians_(J)" title="List of mathematicians (J)">J</a>,
 <a href="/wiki/List_of_mathematicians_(K)" title="List of mathematicians (K)">K</a>,
 <a href="/wiki/List_of_mathematicians_(L)" title="Lis

In [5]:
list_of_links = []

# add "https://en.wikipedia.org/" to front of hrefs to make links universal
for i in rows:
    list_of_links.append("https://en.wikipedia.org/" + str(i)[10:])

# remove extra text in lists    
for j in range(len(list_of_links)):
    list_of_links[j] = list_of_links[j][:56]

list_of_links

['https://en.wikipedia.org/wiki/List_of_mathematicians_(A)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(B)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(C)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(D)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(E)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(F)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(G)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(H)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(I)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(J)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(K)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(L)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(M)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(N)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(O)',
 'https://en.wikipedia.org/wiki/List_of_mathematicians_(P)',
 'https://en.wikipedia.o

In [6]:
# create list of stopwords that should not be included when extracting links from
# the above list of links (i.e. we only want the links sending us to mathematicians)
# these words correspond to links that send us elsewhere
stop_words =  ['None', 'Math', 'Wiki', 'List', 'Outl', 'Port', 'Temp', 'Edit',
               'Help', 'Cate', 'Disc', 'A li', 'You ', "You'", "View", 'Disc',
               'Past', 'Visi', 'Guid', 'Feat', 'Find', 'Load', 'Supp', 'Find',
               'Abou', 'How ', 'Rece', 'Uplo', 'Perm', 'link', 'More', 'Link',
               'Info', 'Prin', 'Danh', 'wmf:']

# create a dictionary holding all mathematicians and their associated wikipedia page links
mathematicians = dict()

for i in list_of_links:
    # Get the Wikipedia page
    req = requests.get(i)
    req = req.text
    
    soup = BeautifulSoup(req, 'html.parser')
    
    for tag in soup.find_all(re.compile("a")):
        if tag.name == 'a':
            link = tag.get('title')
            if link is not None and link[:4] not in stop_words:
                mathematicians.update({link : "https://en.wikipedia.org" + tag.get('href')})
                print(link)
                print(tag)
                print(tag.get('href'))
                print()

Choudum S. A.
<a class="mw-redirect" href="/wiki/Choudum_S._A." title="Choudum S. A.">A., Choudum S.</a>
/wiki/Choudum_S._A.

Asger Aaboe
<a href="/wiki/Asger_Aaboe" title="Asger Aaboe">Aaboe, Asger</a>
/wiki/Asger_Aaboe

Odd Aalen
<a href="/wiki/Odd_Aalen" title="Odd Aalen">Aalen, Odd</a>
/wiki/Odd_Aalen

Stål Aanderaa
<a href="/wiki/St%C3%A5l_Aanderaa" title="Stål Aanderaa">Aanderaa, Stål</a>
/wiki/St%C3%A5l_Aanderaa

Bruno Abakanowicz
<a href="/wiki/Bruno_Abakanowicz" title="Bruno Abakanowicz">Abakanowicz, Bruno</a>
/wiki/Bruno_Abakanowicz

Marco Abate
<a href="/wiki/Marco_Abate" title="Marco Abate">Abate, Marco</a>
/wiki/Marco_Abate

Saeid Abbasbandy
<a href="/wiki/Saeid_Abbasbandy" title="Saeid Abbasbandy">Abbasbandy, Saeid</a>
/wiki/Saeid_Abbasbandy

Maleyka Abbaszadeh
<a href="/wiki/Maleyka_Abbaszadeh" title="Maleyka Abbaszadeh">Abbaszadeh, Maleyka</a>
/wiki/Maleyka_Abbaszadeh

Thomas Kingsmill Abbott
<a href="/wiki/Thomas_Kingsmill_Abbott" title="Thomas Kingsmill Abbott">Abbott

László Babai
<a href="/wiki/L%C3%A1szl%C3%B3_Babai" title="László Babai">Babai, László</a>
/wiki/L%C3%A1szl%C3%B3_Babai

Charles Babbage
<a href="/wiki/Charles_Babbage" title="Charles Babbage">Babbage, Charles</a>
/wiki/Charles_Babbage

Dennis Babbage
<a href="/wiki/Dennis_Babbage" title="Dennis Babbage">Babbage, Dennis</a>
/wiki/Dennis_Babbage

Wealthy Babcock
<a href="/wiki/Wealthy_Babcock" title="Wealthy Babcock">Babcock, Wealthy</a>
/wiki/Wealthy_Babcock

Tytus Babczyński
<a href="/wiki/Tytus_Babczy%C5%84ski" title="Tytus Babczyński">Babczyński, Tytus</a>
/wiki/Tytus_Babczy%C5%84ski

John Babington (mathematician)
<a href="/wiki/John_Babington_(mathematician)" title="John Babington (mathematician)">Babington, John</a>
/wiki/John_Babington_(mathematician)

Esmail Babolian
<a href="/wiki/Esmail_Babolian" title="Esmail Babolian">Babolian, Esmail</a>
/wiki/Esmail_Babolian

Philibert Babou
<a href="/wiki/Philibert_Babou" title="Philibert Babou">Babou, Philibert</a>
/wiki/Philibert_Babou

Eduardo Torroja Caballe
<a href="/wiki/Eduardo_Torroja_Caballe" title="Eduardo Torroja Caballe">Caballe, Eduardo Torroja</a>
/wiki/Eduardo_Torroja_Caballe

Niccolò Cabeo
<a href="/wiki/Niccol%C3%B2_Cabeo" title="Niccolò Cabeo">Cabeo, Niccolò</a>
/wiki/Niccol%C3%B2_Cabeo

Angelina Cabras
<a href="/wiki/Angelina_Cabras" title="Angelina Cabras">Cabras, Angelina</a>
/wiki/Angelina_Cabras

Renato Caccioppoli
<a href="/wiki/Renato_Caccioppoli" title="Renato Caccioppoli">Caccioppoli, Renato</a>
/wiki/Renato_Caccioppoli

Dominique de Caen
<a href="/wiki/Dominique_de_Caen" title="Dominique de Caen">de Caen, Dominique</a>
/wiki/Dominique_de_Caen

Luis Caffarelli
<a href="/wiki/Luis_Caffarelli" title="Luis Caffarelli">Caffarelli, Luis</a>
/wiki/Luis_Caffarelli

Federico Cafiero
<a href="/wiki/Federico_Cafiero" title="Federico Cafiero">Cafiero, Federico</a>
/wiki/Federico_Cafiero

Russel E. Caflisch
<a href="/wiki/Russel_E._Caflisch" title="Russel E. Caflisch">Caflisch, Russel E.</a>
/wiki/Russel_

Weinan E
<a href="/wiki/Weinan_E" title="Weinan E">E, Weinan</a>
/wiki/Weinan_E

Albert Eagle
<a href="/wiki/Albert_Eagle" title="Albert Eagle">Eagle, Albert</a>
/wiki/Albert_Eagle

Samuel Earnshaw
<a href="/wiki/Samuel_Earnshaw" title="Samuel Earnshaw">Earnshaw, Samuel</a>
/wiki/Samuel_Earnshaw

Annie Easley
<a href="/wiki/Annie_Easley" title="Annie Easley">Easley, Annie</a>
/wiki/Annie_Easley

George Eason
<a href="/wiki/George_Eason" title="George Eason">Eason, George</a>
/wiki/George_Eason

Rob Eastaway
<a href="/wiki/Rob_Eastaway" title="Rob Eastaway">Eastaway, Rob</a>
/wiki/Rob_Eastaway

Brian Easton (economist)
<a href="/wiki/Brian_Easton_(economist)" title="Brian Easton (economist)">Easton, Brian</a>
/wiki/Brian_Easton_(economist)

William Bigelow Easton
<a href="/wiki/William_Bigelow_Easton" title="William Bigelow Easton">Easton, William Bigelow</a>
/wiki/William_Bigelow_Easton

Heinz-Dieter Ebbinghaus
<a href="/wiki/Heinz-Dieter_Ebbinghaus" title="Heinz-Dieter Ebbinghaus">Ebb

Steven Gaal
<a href="/wiki/Steven_Gaal" title="Steven Gaal">Gaal, Steven</a>
/wiki/Steven_Gaal

David Gabai
<a href="/wiki/David_Gabai" title="David Gabai">Gabai, David</a>
/wiki/David_Gabai

Ofer Gabber
<a href="/wiki/Ofer_Gabber" title="Ofer Gabber">Gabber, Ofer</a>
/wiki/Ofer_Gabber

Pierre Gabriel
<a href="/wiki/Pierre_Gabriel" title="Pierre Gabriel">Gabriel, Pierre</a>
/wiki/Pierre_Gabriel

Robert Mark Gabriel
<a href="/wiki/Robert_Mark_Gabriel" title="Robert Mark Gabriel">Gabriel, Robert Mark</a>
/wiki/Robert_Mark_Gabriel

Andrei Gabrielov
<a href="/wiki/Andrei_Gabrielov" title="Andrei Gabrielov">Gabrielov, Andrei</a>
/wiki/Andrei_Gabrielov

Christophe Gadbled
<a href="/wiki/Christophe_Gadbled" title="Christophe Gadbled">Gadbled, Christophe</a>
/wiki/Christophe_Gadbled

Sulochana Gadgil
<a href="/wiki/Sulochana_Gadgil" title="Sulochana Gadgil">Gadgil, Sulochana</a>
/wiki/Sulochana_Gadgil

Terence Gaffney
<a href="/wiki/Terence_Gaffney" title="Terence Gaffney">Gaffney, Terence</a>

...

Ahmad Ibn al-Qadi
<a href="/wiki/Ahmad_Ibn_al-Qadi" title="Ahmad Ibn al-Qadi">al-Qadi, Ahmad Ibn</a>
/wiki/Ahmad_Ibn_al-Qadi

Asghar Qadir
<a href="/wiki/Asghar_Qadir" title="Asghar Qadir">Qadir, Asghar</a>
/wiki/Asghar_Qadir

Ahmad al-Qalqashandi
<a href="/wiki/Ahmad_al-Qalqashandi" title="Ahmad al-Qalqashandi">al-Qalqashandi, Ahmad</a>
/wiki/Ahmad_al-Qalqashandi

Xiong Qinglai
<a href="/wiki/Xiong_Qinglai" title="Xiong Qinglai">Qinglai, Xiong</a>
/wiki/Xiong_Qinglai

Edward Schaumberg Quade
<a href="/wiki/Edward_Schaumberg_Quade" title="Edward Schaumberg Quade">Quade, Edward Schaumberg</a>
/wiki/Edward_Schaumberg_Quade

Alfio Quarteroni
<a href="/wiki/Alfio_Quarteroni" title="Alfio Quarteroni">Quarteroni, Alfio</a>
/wiki/Alfio_Quarteroni

Jeremy Quastel
<a href="/wiki/Jeremy_Quastel" title="Jeremy Quastel">Quastel, Jeremy</a>
/wiki/Jeremy_Quastel

Ruy de Queiroz
<a href="/wiki/Ruy_de_Queiroz" title="Ruy de Queiroz">de Queiroz, Ruy</a>
/wiki/Ruy_de_Queiroz

Adolphe Quetelet
<a href="/

Yousef Saad
<a href="/wiki/Yousef_Saad" title="Yousef Saad">Saad, Yousef</a>
/wiki/Yousef_Saad

Donald G. Saari
<a href="/wiki/Donald_G._Saari" title="Donald G. Saari">Saari, Donald G.</a>
/wiki/Donald_G._Saari

Thomas L. Saaty
<a href="/wiki/Thomas_L._Saaty" title="Thomas L. Saaty">Saaty, Thomas L.</a>
/wiki/Thomas_L._Saaty

Claude Sabbah
<a href="/wiki/Claude_Sabbah" title="Claude Sabbah">Sabbah, Claude</a>
/wiki/Claude_Sabbah

Gert Sabidussi
<a href="/wiki/Gert_Sabidussi" title="Gert Sabidussi">Sabidussi, Gert</a>
/wiki/Gert_Sabidussi

Alia Sabur
<a href="/wiki/Alia_Sabur" title="Alia Sabur">Sabur, Alia</a>
/wiki/Alia_Sabur

Giovanni Girolamo Saccheri
<a href="/wiki/Giovanni_Girolamo_Saccheri" title="Giovanni Girolamo Saccheri">Saccheri, Giovanni Girolamo</a>
/wiki/Giovanni_Girolamo_Saccheri

Horst Sachs
<a href="/wiki/Horst_Sachs" title="Horst Sachs">Sachs, Horst</a>
/wiki/Horst_Sachs

Gerald Sacks
<a href="/wiki/Gerald_Sacks" title="Gerald Sacks">Sacks, Gerald</a>
/wiki/Gerald_Sac

Udayana
<a href="/wiki/Udayana" title="Udayana">Udayana</a>
/wiki/Udayana

Kenji Ueno
<a href="/wiki/Kenji_Ueno" title="Kenji Ueno">Ueno, Kenji</a>
/wiki/Kenji_Ueno

Petr Ufimtsev
<a href="/wiki/Petr_Ufimtsev" title="Petr Ufimtsev">Ufimtsev, Petr</a>
/wiki/Petr_Ufimtsev

Hassan Ugail
<a href="/wiki/Hassan_Ugail" title="Hassan Ugail">Ugail, Hassan</a>
/wiki/Hassan_Ugail

Olabisi Ugbebor
<a href="/wiki/Olabisi_Ugbebor" title="Olabisi Ugbebor">Ugbebor, Olabisi</a>
/wiki/Olabisi_Ugbebor

George Uhlenbeck
<a href="/wiki/George_Uhlenbeck" title="George Uhlenbeck">Uhlenbeck, George</a>
/wiki/George_Uhlenbeck

Karen Uhlenbeck
<a href="/wiki/Karen_Uhlenbeck" title="Karen Uhlenbeck">Uhlenbeck, Karen</a>
/wiki/Karen_Uhlenbeck

Gunther Uhlmann
<a href="/wiki/Gunther_Uhlmann" title="Gunther Uhlmann">Uhlmann, Gunther</a>
/wiki/Gunther_Uhlmann

Adrien Ulacq
<a href="/wiki/Adrien_Ulacq" title="Adrien Ulacq">Ulacq, Adrien</a>
/wiki/Adrien_Ulacq

Stanislaw Ulam
<a href="/wiki/Stanislaw_Ulam" title="Stan

Michelle L. Wachs
<a href="/wiki/Michelle_L._Wachs" title="Michelle L. Wachs">Wachs, Michelle L.</a>
/wiki/Michelle_L._Wachs

Takeo Wada
<a href="/wiki/Takeo_Wada" title="Takeo Wada">Wada, Takeo</a>
/wiki/Takeo_Wada

Robert Waddington (mathematician)
<a href="/wiki/Robert_Waddington_(mathematician)" title="Robert Waddington (mathematician)">Waddington, Robert</a>
/wiki/Robert_Waddington_(mathematician)

Bartel Leendert van der Waerden
<a href="/wiki/Bartel_Leendert_van_der_Waerden" title="Bartel Leendert van der Waerden">van der Waerden, Bartel Leendert</a>
/wiki/Bartel_Leendert_van_der_Waerden

'Abd al-'Aziz al-Wafa'i
<a href="/wiki/%27Abd_al-%27Aziz_al-Wafa%27i" title="'Abd al-'Aziz al-Wafa'i">al-Wafa'i, 'Abd al-'Aziz</a>
/wiki/%27Abd_al-%27Aziz_al-Wafa%27i

Klaus Wagner
<a href="/wiki/Klaus_Wagner" title="Klaus Wagner">Wagner, Klaus</a>
/wiki/Klaus_Wagner

Manfred Wagner
<a href="/wiki/Manfred_Wagner" title="Manfred Wagner">Wagner, Manfred</a>
/wiki/Manfred_Wagner

Viktor Wagner
<a 

Naum Ya. Vilenkin
<a href="/wiki/Naum_Ya._Vilenkin" title="Naum Ya. Vilenkin">Ya. Vilenkin, Naum</a>
/wiki/Naum_Ya._Vilenkin

Grigoriy Yablonsky
<a href="/wiki/Grigoriy_Yablonsky" title="Grigoriy Yablonsky">Yablonsky, Grigoriy</a>
/wiki/Grigoriy_Yablonsky

Sergey Yablonsky
<a href="/wiki/Sergey_Yablonsky" title="Sergey Yablonsky">Yablonsky, Sergey</a>
/wiki/Sergey_Yablonsky

Myhailo Yadrenko
<a href="/wiki/Myhailo_Yadrenko" title="Myhailo Yadrenko">Yadrenko, Myhailo</a>
/wiki/Myhailo_Yadrenko

Isaak Yaglom
<a href="/wiki/Isaak_Yaglom" title="Isaak Yaglom">Yaglom, Isaak</a>
/wiki/Isaak_Yaglom

Yajnavalkya
<a href="/wiki/Yajnavalkya" title="Yajnavalkya">Yajnavalkya</a>
/wiki/Yajnavalkya

Evgenii Georgievich D'yakonov
<a href="/wiki/Evgenii_Georgievich_D%27yakonov" title="Evgenii Georgievich D'yakonov">D'yakonov, Evgenii Georgievich</a>
/wiki/Evgenii_Georgievich_D%27yakonov

Vladimir Andreevich Yakubovich
<a href="/wiki/Vladimir_Andreevich_Yakubovich" title="Vladimir Andreevich Yakubovich

In [7]:
mathematicians

{'Roger Joseph Boscovich': 'https://en.wikipedia.org/wiki/Roger_Joseph_Boscovich',
 'Fariba Fahroo': 'https://en.wikipedia.org/wiki/Fariba_Fahroo',
 'Christian Zeller': 'https://en.wikipedia.org/wiki/Christian_Zeller',
 'Feodor Deahna': 'https://en.wikipedia.org/wiki/Feodor_Deahna',
 'Denis Henrion': 'https://en.wikipedia.org/wiki/Denis_Henrion',
 'Yuri Dmitrievich Burago': 'https://en.wikipedia.org/wiki/Yuri_Dmitrievich_Burago',
 'John Hymers': 'https://en.wikipedia.org/wiki/John_Hymers',
 'Alexander Grothendieck': 'https://en.wikipedia.org/wiki/Alexander_Grothendieck',
 'Theodore James Courant': 'https://en.wikipedia.org/wiki/Theodore_James_Courant',
 'Ljubomir Chakaloff': 'https://en.wikipedia.org/wiki/Ljubomir_Chakaloff',
 'Earnshaw Cook': 'https://en.wikipedia.org/wiki/Earnshaw_Cook',
 'Nikolay Bogolyubov': 'https://en.wikipedia.org/wiki/Nikolay_Bogolyubov',
 'C. S. Seshadri': 'https://en.wikipedia.org/wiki/C._S._Seshadri',
 'George F. Pinder': 'https://en.wikipedia.org/wiki/Georg

In [8]:
# count number of mathematicians in list
x = 0
mathematicians_list = []
for i in mathematicians:
    x = x + 1
    mathematicians_list.append(i)
    
print(x)
print(mathematicians_list[:5])

8650
['Roger Joseph Boscovich', 'Fariba Fahroo', 'Christian Zeller', 'Feodor Deahna', 'Denis Henrion']


In [10]:
# create dictionary holding all mathematicians and their wikidata page link
Wikidata_list = dict()

x = 0
for i in mathematicians:
#     time.sleep(.25)
    try:
        req = requests.get(mathematicians[i])
        page = req.text
        soup = BeautifulSoup(page, 'html.parser')

        lister = soup.find_all('a')

        for j in lister:
            if j.get('title') == 'Link to connected data repository item [g]':
                print()
                print(i)
                print(j.get('href'))
                print(x)
                Wikidata_list.update({i : j.get('href')})
                x = x + 1
                
    except Exception: 
        print("Connection refused by the server..")
        print('Sleeping for 5 minutes...')
        time.sleep(30)
        continue

Wikidata_list


Roger Joseph Boscovich
https://www.wikidata.org/wiki/Special:EntityPage/Q310757
0

Fariba Fahroo
https://www.wikidata.org/wiki/Special:EntityPage/Q5435217
1

Christian Zeller
https://www.wikidata.org/wiki/Special:EntityPage/Q72987
2

Feodor Deahna
https://www.wikidata.org/wiki/Special:EntityPage/Q5443711
3

Denis Henrion
https://www.wikidata.org/wiki/Special:EntityPage/Q3022732
4

Yuri Dmitrievich Burago
https://www.wikidata.org/wiki/Special:EntityPage/Q710985
5

John Hymers
https://www.wikidata.org/wiki/Special:EntityPage/Q15452505
6

Alexander Grothendieck
https://www.wikidata.org/wiki/Special:EntityPage/Q77141
7

Theodore James Courant
https://www.wikidata.org/wiki/Special:EntityPage/Q7781851
8

Ljubomir Chakaloff
https://www.wikidata.org/wiki/Special:EntityPage/Q6660963
9

Earnshaw Cook
https://www.wikidata.org/wiki/Special:EntityPage/Q5326959
10

Nikolay Bogolyubov
https://www.wikidata.org/wiki/Special:EntityPage/Q454925
11

C. S. Seshadri
https://www.wikidata.org/wiki/Special:En


Asef Hadjiyev
https://www.wikidata.org/wiki/Special:EntityPage/Q12836122
105

Nikolai Sergeevich Bakhvalov
https://www.wikidata.org/wiki/Special:EntityPage/Q4079811
106

Earl A. Coddington
https://www.wikidata.org/wiki/Special:EntityPage/Q30339637
107

Frederick Parker-Rhodes
https://www.wikidata.org/wiki/Special:EntityPage/Q5498518
108

W. Frahm
https://www.wikidata.org/wiki/Special:EntityPage/Q7945542
109

Solomon W. Golomb
https://www.wikidata.org/wiki/Special:EntityPage/Q1398547
110

Hilary Putnam
https://www.wikidata.org/wiki/Special:EntityPage/Q221697
111

Mikhail Menshikov
https://www.wikidata.org/wiki/Special:EntityPage/Q6849743
112

Alexis Fontaine des Bertins
https://www.wikidata.org/wiki/Special:EntityPage/Q2351493
113

Charles Mathieu Schols
https://www.wikidata.org/wiki/Special:EntityPage/Q5080725
114

Moshe Shaked
https://www.wikidata.org/wiki/Special:EntityPage/Q21151364
115

Augustus William Smith
https://www.wikidata.org/wiki/Special:EntityPage/Q4821574
116

Jean Gast


Bojidar Spiriev
https://www.wikidata.org/wiki/Special:EntityPage/Q3625269
209

Kenneth I. Gross
https://www.wikidata.org/wiki/Special:EntityPage/Q15823364
210

Jean-Pierre Bourguignon
https://www.wikidata.org/wiki/Special:EntityPage/Q1398883
211

Edward Neuman
https://www.wikidata.org/wiki/Special:EntityPage/Q27861834
212

Ludwig Schlesinger
https://www.wikidata.org/wiki/Special:EntityPage/Q72104
213

Johannes Werner
https://www.wikidata.org/wiki/Special:EntityPage/Q76161
214

Cristian S. Calude
https://www.wikidata.org/wiki/Special:EntityPage/Q5186261
215

Harry Swinney
https://www.wikidata.org/wiki/Special:EntityPage/Q527322
216

Giovanni Battista Pisani
https://www.wikidata.org/wiki/Special:EntityPage/Q21208935
217

Rachel Ward (mathematician)
https://www.wikidata.org/wiki/Special:EntityPage/Q30122229
218

Michelle Francl
https://www.wikidata.org/wiki/Special:EntityPage/Q55235
219

Jörg Bewersdorff
https://www.wikidata.org/wiki/Special:EntityPage/Q89025
220

Sandy Green (mathematic


Charles Brenner (mathematician)
https://www.wikidata.org/wiki/Special:EntityPage/Q23856943
311

Sanford L. Segal
https://www.wikidata.org/wiki/Special:EntityPage/Q7417638
312

Henricus Brucaeus
https://www.wikidata.org/wiki/Special:EntityPage/Q109090
313

Juan de Celaya
https://www.wikidata.org/wiki/Special:EntityPage/Q6301222
314

Levon Aghababyan
https://www.wikidata.org/wiki/Special:EntityPage/Q20512160
315

Jaroslav Kurzweil
https://www.wikidata.org/wiki/Special:EntityPage/Q2873450
316

You-Dong Liang
https://www.wikidata.org/wiki/Special:EntityPage/Q20737947
317

Julius Petersen
https://www.wikidata.org/wiki/Special:EntityPage/Q455001
318

Ottaviano Menni
https://www.wikidata.org/wiki/Special:EntityPage/Q18945705
319

Boris M. Schein
https://www.wikidata.org/wiki/Special:EntityPage/Q4945319
320

Gert Sabidussi
https://www.wikidata.org/wiki/Special:EntityPage/Q5553220
321

Bertram Kostant
https://www.wikidata.org/wiki/Special:EntityPage/Q828478
322

Arnaud Denjoy
https://www.wikid


Arthur Rosenthal
https://www.wikidata.org/wiki/Special:EntityPage/Q105005
414

Sydney Chapman (mathematician)
https://www.wikidata.org/wiki/Special:EntityPage/Q711256
415

Boris Weisfeiler
https://www.wikidata.org/wiki/Special:EntityPage/Q451733
416

Marcel Riesz
https://www.wikidata.org/wiki/Special:EntityPage/Q45099
417

John Hammersley
https://www.wikidata.org/wiki/Special:EntityPage/Q1382531
418

W. W. Rouse Ball
https://www.wikidata.org/wiki/Special:EntityPage/Q429858
419

Edgar Frisby
https://www.wikidata.org/wiki/Special:EntityPage/Q5337248
420

Oscar Lanford
https://www.wikidata.org/wiki/Special:EntityPage/Q450589
421

Hans Schneider (mathematician)
https://www.wikidata.org/wiki/Special:EntityPage/Q5650702
422

Vladimir Mazya
https://www.wikidata.org/wiki/Special:EntityPage/Q828834
423

Eugenio Oñate Ibañez de Navarra
https://www.wikidata.org/wiki/Special:EntityPage/Q3816794
424

Deanna Needell
https://www.wikidata.org/wiki/Special:EntityPage/Q29268511
425

Alemdar Hasanoğlu
h

...


Ernst Peschl
https://www.wikidata.org/wiki/Special:EntityPage/Q103198
8261

Zhu Shijie
https://www.wikidata.org/wiki/Special:EntityPage/Q198126
8262

Heinz Prüfer
https://www.wikidata.org/wiki/Special:EntityPage/Q65216
8263

Alfio Quarteroni
https://www.wikidata.org/wiki/Special:EntityPage/Q2644293
8264

Isaac Milner
https://www.wikidata.org/wiki/Special:EntityPage/Q931384
8265

John Jay Gergen
https://www.wikidata.org/wiki/Special:EntityPage/Q720428
8266

Balázs Szegedy
https://www.wikidata.org/wiki/Special:EntityPage/Q19663852
8267

Czesław Olech
https://www.wikidata.org/wiki/Special:EntityPage/Q431842
8268

Tamás Hausel
https://www.wikidata.org/wiki/Special:EntityPage/Q6165077
8269

Shea Zellweger
https://www.wikidata.org/wiki/Special:EntityPage/Q7492151
8270

Václav Láska
https://www.wikidata.org/wiki/Special:EntityPage/Q3495509
8271

Alain-Sol Sznitman
https://www.wikidata.org/wiki/Special:EntityPage/Q2636350
8272

Jean Paul de Gua de Malves
https://www.wikidata.org/wiki/Special:


Marc Thomas
https://www.wikidata.org/wiki/Special:EntityPage/Q6755916
8364

David V. Hinkley
https://www.wikidata.org/wiki/Special:EntityPage/Q5240584
8365

Walter Noll
https://www.wikidata.org/wiki/Special:EntityPage/Q1403491
8366

Andreas Blass
https://www.wikidata.org/wiki/Special:EntityPage/Q4755386
8367

Zoel García de Galdeano
https://www.wikidata.org/wiki/Special:EntityPage/Q9097736
8368

Arima Yoriyuki
https://www.wikidata.org/wiki/Special:EntityPage/Q3135437
8369

Newton da Costa
https://www.wikidata.org/wiki/Special:EntityPage/Q5365379
8370

Tadatoshi Akiba
https://www.wikidata.org/wiki/Special:EntityPage/Q441718
8371

Anry Nersesyan
https://www.wikidata.org/wiki/Special:EntityPage/Q23682759
8372

Andrei Polyanin
https://www.wikidata.org/wiki/Special:EntityPage/Q4371474
8373

Gustav Elfving
https://www.wikidata.org/wiki/Special:EntityPage/Q4351970
8374

Werner Gysin
https://www.wikidata.org/wiki/Special:EntityPage/Q7983400
8375

Heini Halberstam
https://www.wikidata.org/wiki


Carlos Graef Fernández
https://www.wikidata.org/wiki/Special:EntityPage/Q5391183
8466

Umesh Vazirani
https://www.wikidata.org/wiki/Special:EntityPage/Q92805
8467

John Mather (mathematician)
https://www.wikidata.org/wiki/Special:EntityPage/Q440717
8468

Mikhail Leonidovich Gromov
https://www.wikidata.org/wiki/Special:EntityPage/Q353451
8469

Jacqueline Naze Tjøtta
https://www.wikidata.org/wiki/Special:EntityPage/Q17112464
8470

Ronald Fisher bibliography
https://www.wikidata.org/wiki/Special:EntityPage/Q15989760
8471

Konstantin Malkov
https://www.wikidata.org/wiki/Special:EntityPage/Q6429991
8472

Mahendra Sūri
https://www.wikidata.org/wiki/Special:EntityPage/Q6733781
8473

Richard P. Brent
https://www.wikidata.org/wiki/Special:EntityPage/Q93042
8474

Naum Z. Shor
https://www.wikidata.org/wiki/Special:EntityPage/Q457430
8475

Yousef Saad
https://www.wikidata.org/wiki/Special:EntityPage/Q8059044
8476

William B. Bonnor
https://www.wikidata.org/wiki/Special:EntityPage/Q15994314
8477




Theodorus of Cyrene
https://www.wikidata.org/wiki/Special:EntityPage/Q712328
8569

Athanasios Papoulis
https://www.wikidata.org/wiki/Special:EntityPage/Q3567099
8570

Alfred Enneper
https://www.wikidata.org/wiki/Special:EntityPage/Q68521
8571

Herman Müntz
https://www.wikidata.org/wiki/Special:EntityPage/Q91662
8572

Michael Heath (computer scientist)
https://www.wikidata.org/wiki/Special:EntityPage/Q14492478
8573

James Eells
https://www.wikidata.org/wiki/Special:EntityPage/Q1680331
8574

Edmund Husserl
https://www.wikidata.org/wiki/Special:EntityPage/Q58586
8575

Joseph Kruskal
https://www.wikidata.org/wiki/Special:EntityPage/Q983361
8576

George H. Mealy
https://www.wikidata.org/wiki/Special:EntityPage/Q1507472
8577

Alain Glavieux
https://www.wikidata.org/wiki/Special:EntityPage/Q1460529
8578

Ebenezer Cunningham
https://www.wikidata.org/wiki/Special:EntityPage/Q951453
8579

Carlo Alberto Castigliano
https://www.wikidata.org/wiki/Special:EntityPage/Q983318
8580

Edgar Gilbert
http

{'Roger Joseph Boscovich': 'https://www.wikidata.org/wiki/Special:EntityPage/Q310757',
 'Emma Previato': 'https://www.wikidata.org/wiki/Special:EntityPage/Q19321847',
 'Feodor Deahna': 'https://www.wikidata.org/wiki/Special:EntityPage/Q5443711',
 'Denis Henrion': 'https://www.wikidata.org/wiki/Special:EntityPage/Q3022732',
 'Henri Delannoy': 'https://www.wikidata.org/wiki/Special:EntityPage/Q3130590',
 'John Hymers': 'https://www.wikidata.org/wiki/Special:EntityPage/Q15452505',
 'Alexander Grothendieck': 'https://www.wikidata.org/wiki/Special:EntityPage/Q77141',
 'Theodore James Courant': 'https://www.wikidata.org/wiki/Special:EntityPage/Q7781851',
 'Ljubomir Chakaloff': 'https://www.wikidata.org/wiki/Special:EntityPage/Q6660963',
 'Earnshaw Cook': 'https://www.wikidata.org/wiki/Special:EntityPage/Q5326959',
 'Nikolay Bogolyubov': 'https://www.wikidata.org/wiki/Special:EntityPage/Q454925',
 'Henry W. Gould': 'https://www.wikidata.org/wiki/Special:EntityPage/Q5729644',
 'C. S. Seshadri'

In [11]:
len(Wikidata_list)

8643

In [12]:
Wikidata_list

{'Roger Joseph Boscovich': 'https://www.wikidata.org/wiki/Special:EntityPage/Q310757',
 'Emma Previato': 'https://www.wikidata.org/wiki/Special:EntityPage/Q19321847',
 'Feodor Deahna': 'https://www.wikidata.org/wiki/Special:EntityPage/Q5443711',
 'Denis Henrion': 'https://www.wikidata.org/wiki/Special:EntityPage/Q3022732',
 'Henri Delannoy': 'https://www.wikidata.org/wiki/Special:EntityPage/Q3130590',
 'John Hymers': 'https://www.wikidata.org/wiki/Special:EntityPage/Q15452505',
 'Alexander Grothendieck': 'https://www.wikidata.org/wiki/Special:EntityPage/Q77141',
 'Theodore James Courant': 'https://www.wikidata.org/wiki/Special:EntityPage/Q7781851',
 'Ljubomir Chakaloff': 'https://www.wikidata.org/wiki/Special:EntityPage/Q6660963',
 'Earnshaw Cook': 'https://www.wikidata.org/wiki/Special:EntityPage/Q5326959',
 'Nikolay Bogolyubov': 'https://www.wikidata.org/wiki/Special:EntityPage/Q454925',
 'Henry W. Gould': 'https://www.wikidata.org/wiki/Special:EntityPage/Q5729644',
 'C. S. Seshadri'

In [13]:
# create dataframe from dictionary
mathematicians_df = pd.DataFrame.from_dict(Wikidata_list, orient='index')
mathematicians_df = mathematicians_df.reset_index(drop=False)
mathematicians_df.columns = ['mathematicians', 'links']

mathematicians_df

mathematicians  \
0              Roger Joseph Boscovich   
1                       Emma Previato   
2                       Feodor Deahna   
3                       Denis Henrion   
4                      Henri Delannoy   
5                         John Hymers   
6              Alexander Grothendieck   
7              Theodore James Courant   
8                  Ljubomir Chakaloff   
9                       Earnshaw Cook   
10                 Nikolay Bogolyubov   
11                     Henry W. Gould   
12                     C. S. Seshadri   
13                   George F. Pinder   
14                   Roman Holowinsky   
15                     Johannes Hudde   
16                       Morris Kline   
17                       Thomas Wolff   
18                      Joseph Lipman   
19            John Fox (statistician)   
20                     Martin Bridson   
21    Matthew Stewart (mathematician)   
22                       Uriel Frisch   
23                   Gábor Korchmáros   
24                   Dionigi Galletto   
25                  Quirico Filopanti   
26                  Jeffery J. Leader   
27                        Thomas Rudd   
28                 Elon Lindenstrauss   
29                       Yitang Zhang   
...                               ...   
8613                    Hermann Brunn   
8614                  Judith Grabiner   
8615                    Isaac Namioka   
8616                       Iranshahri   
8617    Martha Isabel Fandiño Pinilla   
8618                  Laurence Wolsey   
8619           Adolph Winkler Goodman   
8620                     Mina Teicher   
8621      Askold Ivanovich Vinogradov   
8622              Ottavio Scarlattini   
8623               James E. Humphreys   
8624                  Maurice Princet   
8625                     Steven Vajda   
8626                László Fejes Tóth   
8627                  Anatoly Vershik   
8628                      Mu-Tao Wang   
8629                       Uwe Storch   
8630                 Bernard Teissier   
8631                    Victor Isakov   
8632            Raymond Woodard Brink   
8633                 Arnaud Beauville   
8634                  Michele Cipolla   
8635    James Crowley (mathematician)   
8636                     Iain S. Duff   
8637                   Ralph Henstock   
8638           Hugh Hamilton (bishop)   
8639                     Boáz Klartag   
8640                  Alain M. Robert   
8641               Paul C. Rosenbloom   
8642                  Edward O. Thorp   

                                                  links  
0     https://www.wikidata.org/wiki/Special:EntityPa...  
1     https://www.wikidata.org/wiki/Special:EntityPa...  
2     https://www.wikidata.org/wiki/Special:EntityPa...  
3     https://www.wikidata.org/wiki/Special:EntityPa...  
4     https://www.wikidata.org/wiki/Special:EntityPa...  
5     https://www.wikidata.org/wiki/Special:EntityPa...  
6     https://www.wikidata.org/wiki/Special:EntityPa...  
7     https://www.wikidata.org/wiki/Special:EntityPa...  
8     https://www.wikidata.org/wiki/Special:EntityPa...  
9     https://www.wikidata.org/wiki/Special:EntityPa...  
10    https://www.wikidata.org/wiki/Special:EntityPa...  
11    https://www.wikidata.org/wiki/Special:EntityPa...  
12    https://www.wikidata.org/wiki/Special:EntityPa...  
13    https://www.wikidata.org/wiki/Special:EntityPa...  
14    https://www.wikidata.org/wiki/Special:EntityPa...  
15    https://www.wikidata.org/wiki/Special:EntityPa...  
16    https://www.wikidata.org/wiki/Special:EntityPa...  
17    https://www.wikidata.org/wiki/Special:EntityPa...  
18    https://www.wikidata.org/wiki/Special:EntityPa...  
19    https://www.wikidata.org/wiki/Special:EntityPa...  
20    https://www.wikidata.org/wiki/Special:EntityPa...  
21    https://www.wikidata.org/wiki/Special:EntityPa...  
22    https://www.wikidata.org/wiki/Special:EntityPa...  
23    https://www.wikidata.org/wiki/Special:EntityPa...  
24    https://www.wikidata.org

In [14]:
# create function that retrieves information from Wikidata page in a dictionary format
def getValues(link):
    req = requests.get(link)
    page = req.text
    soup = BeautifulSoup(page, 'html.parser')

    # remove all initially collapsed divs from text (avoids a lot of uneccessary info)
    for div in soup.find_all("div", {'class':'wikibase-statementview-references wikibase-initially-collapsed'}): 
        div.decompose()

    # find all divs that contain column info, then put it into a list
    container_tag = soup.find_all('div', class_="wikibase-statementgroupview-property-label")
    columns = []
    for container in container_tag:
        columns.append(container.text)

    # find all divs that contain value info
    container_tag = soup.find_all('div', class_='wikibase-statementlistview')
    values = []

    # find all divs within value info, then put those into a sub-list
    # sub-list is necessary because some columns have multiple values
    for container in container_tag:
        value = container.find_all('div', class_='wikibase-snakview-value wikibase-snakview-variation-valuesnak')
        holder = []
        for i in value:
            i = i.text.replace('\r', '').replace('\n', '')
            holder.append(i)
        values.append(holder)
        
    return dict(zip(columns, values))

getValues('https://www.wikidata.org/wiki/Special:EntityPage/Q212063')

{'BnF ID': ['11924501z'],
 'CANTIC-ID': ['a10372544'],
 'Commons category': ['Jean-Pierre Serre'],
 'Encyclopædia Britannica Online ID': ['biography/Jean-Pierre-Serre'],
 'Erdős number': ['2±0'],
 'FAST ID': ['1440365'],
 'Fellow of the Royal Society ID': ['jean-pierre-serre-12253'],
 'Freebase ID': ['/m/01d47g'],
 'GND ID': ['142283126'],
 'ISNI': ['0000 0001 2137 1909'],
 'Library of Congress authority identifier': ['n79060186'],
 'MacTutor id (biographies)': ['Serre'],
 'Mathematics Genealogy Project ID': ['34222'],
 'Munzinger IBA': ['00000024649'],
 'NDL Auth ID': ['00456134'],
 'NE.se ID': ['jean-pierre-serre'],
 'NKCR AUT ID': ['mzk2003213616'],
 'NUKAT (WarsawU) authorities': ['n97008994'],
 'National Thesaurus for Author Names ID': ['071831401'],
 'Quora topic ID': ['Jean-Pierre-Serre'],
 'SELIBR': ['228529'],
 'SUDOC authorities': ['027133222'],
 'Social Networks and Archival Context ID': ['w6rf7xj4'],
 'VIAF ID': ['66473477'],
 "Who's Who in France biography ID": ['jean-pier

In [15]:
# function that creates new columns from the dictionary produced by the getValues function
def addingColumns(df):
    dictionary = getValues(df.links)
    print(df.mathematicians)
    print(df.links)
    print('columns: ', len(dictionary))
    print()
    for column in dictionary:
        df[column] = dictionary.get(column)
    return df
    
# apply addingColumns function to entire dataframe
mathematicians_df_2 = mathematicians_df.apply(addingColumns, axis=1)
mathematicians_df_2

Roger Joseph Boscovich
https://www.wikidata.org/wiki/Special:EntityPage/Q310757
columns:  57

Roger Joseph Boscovich
https://www.wikidata.org/wiki/Special:EntityPage/Q310757
columns:  57

Emma Previato
https://www.wikidata.org/wiki/Special:EntityPage/Q19321847
columns:  22

Feodor Deahna
https://www.wikidata.org/wiki/Special:EntityPage/Q5443711
columns:  9

Denis Henrion
https://www.wikidata.org/wiki/Special:EntityPage/Q3022732
columns:  16

Henri Delannoy
https://www.wikidata.org/wiki/Special:EntityPage/Q3130590
columns:  18

John Hymers
https://www.wikidata.org/wiki/Special:EntityPage/Q15452505
columns:  20

Alexander Grothendieck
https://www.wikidata.org/wiki/Special:EntityPage/Q77141
columns:  47

Theodore James Courant
https://www.wikidata.org/wiki/Special:EntityPage/Q7781851
columns:  10

Ljubomir Chakaloff
https://www.wikidata.org/wiki/Special:EntityPage/Q6660963
columns:  15

Earnshaw Cook
https://www.wikidata.org/wiki/Special:EntityPage/Q5326959
columns:  5

Nikolay Bogolyubov

John Blagrave
https://www.wikidata.org/wiki/Special:EntityPage/Q3710116
columns:  16

Ben Green (mathematician)
https://www.wikidata.org/wiki/Special:EntityPage/Q792628
columns:  24

Adrian Bowyer
https://www.wikidata.org/wiki/Special:EntityPage/Q1981681
columns:  16

William of Heytesbury
https://www.wikidata.org/wiki/Special:EntityPage/Q1856133
columns:  18

John Stillwell
https://www.wikidata.org/wiki/Special:EntityPage/Q616266
columns:  26

Helmut Hasse
https://www.wikidata.org/wiki/Special:EntityPage/Q61768
columns:  37

Klara Dan von Neumann
https://www.wikidata.org/wiki/Special:EntityPage/Q14100
columns:  14

Valerie Isham
https://www.wikidata.org/wiki/Special:EntityPage/Q7911289
columns:  14

Stefan Ralescu
https://www.wikidata.org/wiki/Special:EntityPage/Q7606246
columns:  11

Jay Kappraff
https://www.wikidata.org/wiki/Special:EntityPage/Q11102007
columns:  7

Irvin Cohen
https://www.wikidata.org/wiki/Special:EntityPage/Q1673262
columns:  14

Asef Hadjiyev
https://www.wikidata

Gustav Herglotz
https://www.wikidata.org/wiki/Special:EntityPage/Q73015
columns:  36

Sigve Tjøtta
https://www.wikidata.org/wiki/Special:EntityPage/Q7513374
columns:  13

Roger Lyndon
https://www.wikidata.org/wiki/Special:EntityPage/Q3439226
columns:  24

Ludwig Boltzmann
https://www.wikidata.org/wiki/Special:EntityPage/Q84296
columns:  70

Brian Kuttner
https://www.wikidata.org/wiki/Special:EntityPage/Q4964391
columns:  9

Zdzisław Krygowski
https://www.wikidata.org/wiki/Special:EntityPage/Q3850336
columns:  10

Francis Guthrie
https://www.wikidata.org/wiki/Special:EntityPage/Q1441533
columns:  17

Curt Meyer
https://www.wikidata.org/wiki/Special:EntityPage/Q91363
columns:  23

Thomas Muirhead Flett
https://www.wikidata.org/wiki/Special:EntityPage/Q7792603
columns:  14

Gerhard Hochschild
https://www.wikidata.org/wiki/Special:EntityPage/Q371662
columns:  26

Len Cook
https://www.wikidata.org/wiki/Special:EntityPage/Q6521727
columns:  9

Bojidar Spiriev
https://www.wikidata.org/wiki/Sp

Frank J. Ayres
https://www.wikidata.org/wiki/Special:EntityPage/Q16971195
columns:  11

Paul Dedecker
https://www.wikidata.org/wiki/Special:EntityPage/Q3371002
columns:  10

Lev Schnirelmann
https://www.wikidata.org/wiki/Special:EntityPage/Q385207
columns:  26

Peter G. Casazza
https://www.wikidata.org/wiki/Special:EntityPage/Q29453055
columns:  4

Raphael Levi Hannover
https://www.wikidata.org/wiki/Special:EntityPage/Q96517
columns:  18

Kurt Leichtweiss
https://www.wikidata.org/wiki/Special:EntityPage/Q98036
columns:  19

Walter Foster (mathematician)
https://www.wikidata.org/wiki/Special:EntityPage/Q7964863
columns:  11

Tadeusz Kotarbiński
https://www.wikidata.org/wiki/Special:EntityPage/Q714839
columns:  38

David Minda
https://www.wikidata.org/wiki/Special:EntityPage/Q5237603
columns:  8

Claudia Zaslavsky
https://www.wikidata.org/wiki/Special:EntityPage/Q5129285
columns:  13

Edward H. Simpson
https://www.wikidata.org/wiki/Special:EntityPage/Q1292590
columns:  10

Dwight Duffus


Sergiu Hart
https://www.wikidata.org/wiki/Special:EntityPage/Q7454483
columns:  16

Axel Thue
https://www.wikidata.org/wiki/Special:EntityPage/Q372010
columns:  31

Hermann Bondi
https://www.wikidata.org/wiki/Special:EntityPage/Q380235
columns:  36

Marcel-Paul Schützenberger
https://www.wikidata.org/wiki/Special:EntityPage/Q1384896
columns:  33

Alexey Gorgidze
https://www.wikidata.org/wiki/Special:EntityPage/Q16638172
columns:  14

Evgeny Yakovlevich Remez
https://www.wikidata.org/wiki/Special:EntityPage/Q919074
columns:  21

Marie-Françoise Roy
https://www.wikidata.org/wiki/Special:EntityPage/Q1116827
columns:  25

Felix Klein
https://www.wikidata.org/wiki/Special:EntityPage/Q76641
columns:  70

Robert Simpson Woodward
https://www.wikidata.org/wiki/Special:EntityPage/Q3709961
columns:  19

Peter Balazs (mathematician)
https://www.wikidata.org/wiki/Special:EntityPage/Q87616
columns:  16

Umaswati
https://www.wikidata.org/wiki/Special:EntityPage/Q1777897
columns:  8

Arthur Stanley Ra

...

Louis-Benjamin Francœur
https://www.wikidata.org/wiki/Special:EntityPage/Q323650
columns:  41

Henri Poincaré
https://www.wikidata.org/wiki/Special:EntityPage/Q81082
columns:  76

Misir Mardanov
https://www.wikidata.org/wiki/Special:EntityPage/Q4281251
columns:  11

Nicolas Chuquet
https://www.wikidata.org/wiki/Special:EntityPage/Q1986557
columns:  24

Gino Fano
https://www.wikidata.org/wiki/Special:EntityPage/Q726861
columns:  29

Bruce C. Berndt
https://www.wikidata.org/wiki/Special:EntityPage/Q381343
columns:  28

Daniel Bernoulli
https://www.wikidata.org/wiki/Special:EntityPage/Q122366
columns:  56

William Threlfall
https://www.wikidata.org/wiki/Special:EntityPage/Q87109
columns:  31

Jean-Marie Souriau
https://www.wikidata.org/wiki/Special:EntityPage/Q1384927
columns:  24

H. B. Walikar
https://www.wikidata.org/wiki/Special:EntityPage/Q5628085
columns:  6

Xin-She Yang
https://www.wikidata.org/wiki/Special:EntityPage/Q11108947
columns:  8

Günter Asser
https://www.wikidata.org/wi

David Friesenhausen
https://www.wikidata.org/wiki/Special:EntityPage/Q96680
columns:  13

Johann II Bernoulli
https://www.wikidata.org/wiki/Special:EntityPage/Q123994
columns:  29

Alexander Weinstein
https://www.wikidata.org/wiki/Special:EntityPage/Q276980
columns:  24

Hōjō Tokiyuki (Scouting)
https://www.wikidata.org/wiki/Special:EntityPage/Q5965200
columns:  16

Zhang Heng
https://www.wikidata.org/wiki/Special:EntityPage/Q197206
columns:  23

William Leybourn
https://www.wikidata.org/wiki/Special:EntityPage/Q8014557
columns:  20

Boris Zilber
https://www.wikidata.org/wiki/Special:EntityPage/Q893805
columns:  17

Christoffer Dybvad
https://www.wikidata.org/wiki/Special:EntityPage/Q5111653
columns:  9

Geoffrey Horrocks
https://www.wikidata.org/wiki/Special:EntityPage/Q5534681
columns:  10

Edmund Schuster
https://www.wikidata.org/wiki/Special:EntityPage/Q15989592
columns:  6

Yuan-Shih Chow
https://www.wikidata.org/wiki/Special:EntityPage/Q8060007
columns:  13

Andreas Speiser
https

Didier Dubois (mathematician)
https://www.wikidata.org/wiki/Special:EntityPage/Q5274170
columns:  14

L. H. C. Tippett
https://www.wikidata.org/wiki/Special:EntityPage/Q3830305
columns:  19

Peter Gustav Lejeune Dirichlet
https://www.wikidata.org/wiki/Special:EntityPage/Q29193
columns:  50

Werner Weber (mathematician)
https://www.wikidata.org/wiki/Special:EntityPage/Q13140357
columns:  20

Eugenio Calabi
https://www.wikidata.org/wiki/Special:EntityPage/Q4922
columns:  27

Jean-Marc Deshouillers
https://www.wikidata.org/wiki/Special:EntityPage/Q1323950
columns:  19

Maryna Viazovska
https://www.wikidata.org/wiki/Special:EntityPage/Q23721911
columns:  21

Abraham Wald
https://www.wikidata.org/wiki/Special:EntityPage/Q240772
columns:  33

Francesco Barozzi
https://www.wikidata.org/wiki/Special:EntityPage/Q657600
columns:  30

Hayyim Selig Slonimski
https://www.wikidata.org/wiki/Special:EntityPage/Q976296
columns:  28

Anton Felkel
https://www.wikidata.org/wiki/Special:EntityPage/Q589271


Matthew Raper
https://www.wikidata.org/wiki/Special:EntityPage/Q3297579
columns:  11

Carlisle Adams
https://www.wikidata.org/wiki/Special:EntityPage/Q2939134
columns:  7

Fritz Carlson
https://www.wikidata.org/wiki/Special:EntityPage/Q5504887
columns:  27

Boris Levit
https://www.wikidata.org/wiki/Special:EntityPage/Q4945313
columns:  7

Lars Ahlfors
https://www.wikidata.org/wiki/Special:EntityPage/Q211642
columns:  42

Elisabeth Klein
https://www.wikidata.org/wiki/Special:EntityPage/Q5361492
columns:  12

Wim Sweldens
https://www.wikidata.org/wiki/Special:EntityPage/Q8023488
columns:  8

Philip Candelas
https://www.wikidata.org/wiki/Special:EntityPage/Q2086091
columns:  17

Howard B. Myers
https://www.wikidata.org/wiki/Special:EntityPage/Q5919021
columns:  10

Albert Châtelet
https://www.wikidata.org/wiki/Special:EntityPage/Q628694
columns:  33

Lucy Joan Slater
https://www.wikidata.org/wiki/Special:EntityPage/Q6698381
columns:  20

Baden Powell (mathematician)
https://www.wikidata.o

365chess player ID ACM Digital Library author ID ADK member ID  \
0                   NaN                           NaN           NaN   
1                   NaN                           NaN           NaN   
2                   NaN                           NaN           NaN   
3                   NaN                           NaN           NaN   
4                   NaN                           NaN           NaN   
5                   NaN                           NaN           NaN   
6                   NaN                           NaN           NaN   
7                   NaN                           NaN           NaN   
8                   NaN                           NaN           NaN   
9                   NaN                           NaN           NaN   
10                  NaN                           NaN           NaN   
11                  NaN                           NaN           NaN   
12                  NaN                           NaN           NaN   
13                  NaN                           NaN           NaN   
14                  NaN                           NaN           NaN   
15                  NaN                           NaN           NaN   
16                  NaN                           NaN           NaN   
17                  NaN                           NaN           NaN   
18                  NaN                           NaN           NaN   
19                  NaN                           NaN           NaN   
20                  NaN                           NaN           NaN   
21                  NaN                           NaN           NaN   
22                  NaN                           NaN           NaN   
23                  NaN                           NaN           NaN   
24                  NaN                           NaN           NaN   
25                  NaN                           NaN           NaN   
26                  NaN                           NaN           NaN   
27                  NaN                           NaN           NaN   
28                  NaN                           NaN           NaN   
29                  NaN                           NaN           NaN   
...                 ...                           ...           ...   
8613                NaN                           NaN           NaN   
8614                NaN                           NaN           NaN   
8615                NaN                           NaN           NaN   
8616                NaN                           NaN           NaN   
8617                NaN                           NaN           NaN   
8618                NaN                           NaN           NaN   
8619                NaN                           NaN           NaN   
8620                NaN                           NaN           NaN   
8621                NaN                           NaN           NaN   
8622                NaN                           NaN           NaN   
8623                NaN                           NaN           NaN   
8624                NaN                           NaN           NaN   
8625                NaN                           NaN           NaN   
8626                NaN                           NaN           NaN   
8627                NaN                           NaN           NaN   
8628                NaN                           NaN           NaN   
8629                NaN                           NaN           NaN   
8630                NaN                           NaN           NaN   
8631                NaN                           NaN           NaN   
8632                NaN                           NaN           NaN   
8633                NaN                           NaN           NaN   
8634                NaN                           NaN           NaN   
8635                NaN                           NaN           NaN   
8636                NaN                           NaN           NaN   
8637                NaN      

In [16]:
mathematicians_df_2.shape

8643

In [19]:
mathematicians_df_2.to_csv('data_uncleaned.csv', index=False)